In [1]:
%load_ext autoreload
%autoreload 2

import tensorflow as tf

In [2]:
def parse_tfrecord_tf(record):
    features = tf.io.parse_single_example(record, features={
        'shape': tf.io.FixedLenFeature([3], tf.int64),
        'data': tf.io.FixedLenFeature([], tf.string)})
    data = tf.io.decode_raw(features['data'], tf.uint8)
    return tf.transpose(tf.reshape(data, features['shape']), [1, 2, 0]).numpy()

In [3]:
import csv
import os
from PIL import Image
import shutil
import subprocess

import torch
from diffusers import StableDiffusionXLImg2ImgPipeline

c:\Users\colin\AppData\Local\Programs\Python\Python310\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [4]:

pipe = StableDiffusionXLImg2ImgPipeline.from_pretrained(
    "stabilityai/stable-diffusion-xl-refiner-1.0", torch_dtype=torch.float16, variant="fp16", use_safetensors=True
)
pipe = pipe.to("cuda")

Loading pipeline components...: 100%|██████████| 5/5 [00:00<00:00,  6.91it/s]


In [5]:
def check_group(group: str, classification: list):
    if group == "Old&Asian":
        return classification[2] == "Asian" and classification[4] == "70+"
    elif group == "Young&Asian":
        return classification[2] == "Asian" and classification[4] == "20-29"
    elif group == "Old&non-Asian":
        return classification[2] != "Asian" and classification[4] == "70+"
    elif group == "Young&non-Asian":
        return classification[2] != "Asian" and classification[4] == "20-29"
    return False

In [6]:
raw_dataset = tf.data.TFRecordDataset("./celebahq/celebahq-r09.tfrecords")

prompts = {
    "Old&Asian": "120 years old human, Asian, natural image, sharp, DSLR",
    "Old&non-Asian": "120 years old human, natural image, sharp, DSLR",
    "Young&Asian": "20 years old human, Asian, natural image, sharp, DSLR",
    "Young&non-Asian": "20 years old human, natural image, sharp, DSLR"
}
negative_prompt = "ugly, deformed, fake, caricature"

guidance_scales = [8.5, 9.5, 10.5, 11.5, 12.5]

for i, raw_record in enumerate(raw_dataset):
    class_correct = False
    for group, prompt in prompts.items():
        for guidance_scale in guidance_scales:
            print(f"{i} {group} {guidance_scale}")
            with open('FairFace/tmp/tmp.csv', 'w') as f:
                f.write("img_path\n")

            init_image = Image.fromarray(parse_tfrecord_tf(raw_record)).convert('RGB')
            image = pipe(prompt, image=init_image, strength=0.4, guidance_scale=guidance_scale, negative_prompt=negative_prompt).images[0]

            save_path = os.path.join('FairFace/tmp/image', f"tmp.png")
            image.save(save_path)

            with open("FairFace/tmp/tmp.csv", 'a') as f:
                f.write(f"{save_path}\n")

            subprocess.run(['python', 'predict.py', '--csv', 'tmp/tmp.csv'], cwd="FairFace")
            
            with open('FairFace/test_outputs.csv') as f:
                reader = csv.reader(f)
                for row in reader:
                    class_correct = check_group(group, row)
        
            if class_correct:
                shutil.move(save_path, os.path.join('FairFace/tmp/images', group, f"{i}.png"))
                break
        
        if not class_correct:
            print(f"skipping {i}")
            break

    if not class_correct:
        continue

    for group in prompts.keys():
        save_path = os.path.join('FairFace/tmp/images', group, f"{i}.png")
        shutil.move(save_path, os.path.join('synthetic_images', group))


0 Old&Asian 8.5


100%|██████████| 20/20 [00:01<00:00, 13.40it/s]


0 Old&Asian 9.5


100%|██████████| 20/20 [00:01<00:00, 14.90it/s]


0 Old&Asian 10.5


...

2917 Old&non-Asian 8.5


100%|██████████| 20/20 [00:01<00:00, 14.45it/s]


2917 Old&non-Asian 9.5


  0%|          | 0/20 [00:00<?, ?it/s]


KeyboardInterrupt: 